In [1]:
import numpy as np
import pandas as pd
import datetime as dt
import plotly.express as px
import plotly.graph_objects as go
from scipy.optimize import curve_fit

In [2]:
etas = pd.read_csv('datasets\\ModifiedETAS.csv', sep=',', lineterminator='\n')

#magnitude filtering
etas = etas[etas['mag'] > 3]
etas['date'] = pd.to_datetime(etas['date'])

#some cleaning
etas['aftershock'] = etas['aftershock\r']
etas = etas.drop(columns='aftershock\r')
etas['aftershock'] = etas['aftershock'].str.replace('\r', '')

# Determine the start and end dates of the dataset
start_date = etas['date'].min()
end_date = etas['date'].max()

In [3]:
etas.head()

Unnamed: 0       date         year  longitude  latitude   mag       z  \
0           0 1960-01-02  1960.006741  -121.7122   37.3552  4.68  8.3275   
1           1 1960-01-03  1960.009279  -118.3268   34.3443  3.73  7.5910   
2           2 1960-01-03  1960.009778  -117.4833   33.7307  3.53  6.5357   
3           3 1960-01-05  1960.016158  -116.7325   33.7002  3.61  6.4911   
4           4 1960-01-06  1960.017534  -116.3410   33.9390  3.67  9.3259   

  aftershock  
0          b  
1        2.0  
2          b  
3          b  
4          b

In [4]:
aftershock = np.array(etas['aftershock'])
print(aftershock)

['b' '2.0' 'b' ... 'b' 'b' 'b']


In [5]:
def split_decimal_strings(decimal_strings):
    before_decimal = []
    after_decimal = []
    
    for num_str in decimal_strings:
        parts = num_str.split('.')
        before_decimal.append(int(parts[0]))
        after_decimal.append(int(parts[1]))
    
    return before_decimal, after_decimal

In [6]:
aftershock_vals = np.array([str(x) for x in aftershock if isinstance(x, str) and x.replace('.', '', 1).isdigit()])
print(aftershock_vals)


['2.0' '18.0' '18.1' ... '17682.2' '17682.3' '17686.0']


In [7]:
mainshocks, aftershocks = split_decimal_strings(aftershock_vals)
print(mainshocks)
print(aftershocks)

[2, 18, 18, 42, 42, 49, 49, 49, 84, 84, 102, 102, 102, 102, 123, 129, 131, 131, 145, 145, 145, 152, 157, 158, 160, 160, 160, 160, 160, 160, 160, 160, 160, 160, 160, 160, 160, 181, 183, 183, 183, 184, 184, 184, 184, 208, 216, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 236, 252, 252, 252, 256, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 287, 290, 290, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 301, 326, 333, 341, 346, 346, 346, 346, 346, 346, 346, 353, 353, 353, 377, 378, 378, 378, 379, 379, 393, 393, 401, 418, 418, 418, 418, 418, 418, 418, 418, 454, 471, 482, 482, 482, 482, 482, 482, 482, 482, 482, 482, 484, 484, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 492, 

In [8]:
unique_values, counts = np.unique(mainshocks, return_counts=True)

sorted_indices = np.argsort(-counts)  # Reverse sort indices
sorted_counts = counts[sorted_indices]
sorted_values = unique_values[sorted_indices]
print("Top 10 most common mainshockss:")
for i in range(min(10, len(sorted_values))):
    print(f"{sorted_values[i]}: {sorted_counts[i]} occurrences")

Top 10 most common mainshockss:
3820: 1890 occurrences
14341: 1471 occurrences
14770: 1434 occurrences
5246: 545 occurrences
910: 351 occurrences
12293: 270 occurrences
492: 253 occurrences
9685: 222 occurrences
12599: 201 occurrences
2561: 174 occurrences


In [9]:
unique_values, counts = np.unique(aftershocks, return_counts=True)

sorted_indices = np.argsort(-counts)  
sorted_counts = counts[sorted_indices]
sorted_values = unique_values[sorted_indices]
print("Top 10 most common aftershocks:")
for i in range(min(10, len(sorted_values))):
    print(f"{sorted_values[i+1]}: {sorted_counts[i+1]} occurrences")

Top 10 most common aftershocks:
1: 676 occurrences
2: 454 occurrences
3: 350 occurrences
4: 283 occurrences
5: 234 occurrences
6: 206 occurrences
7: 178 occurrences
8: 158 occurrences
9: 143 occurrences
10: 129 occurrences


In [10]:
unique_values, counts = np.unique(mainshocks, return_counts=True)
num_aftershocks = dict(zip(unique_values, counts))
mode_index = np.argmax(counts)
mode = unique_values[mode_index]

print("Number of Aftershocks:", num_aftershocks)

Number of Aftershocks: {2: 1, 18: 2, 42: 2, 49: 3, 84: 2, 102: 4, 123: 1, 129: 1, 131: 2, 145: 3, 152: 1, 157: 1, 158: 1, 160: 13, 181: 1, 183: 3, 184: 4, 208: 1, 216: 1, 236: 25, 252: 3, 256: 1, 287: 19, 290: 2, 301: 27, 326: 1, 333: 1, 341: 1, 346: 7, 353: 3, 377: 1, 378: 3, 379: 2, 393: 2, 401: 1, 418: 8, 454: 1, 471: 1, 482: 10, 484: 2, 492: 253, 515: 2, 524: 2, 534: 1, 545: 3, 559: 2, 562: 45, 581: 1, 611: 4, 618: 1, 626: 1, 652: 24, 713: 1, 724: 2, 725: 3, 774: 2, 789: 1, 809: 1, 811: 3, 830: 4, 831: 5, 850: 1, 887: 1, 910: 351, 911: 1, 940: 8, 945: 1, 973: 1, 974: 1, 975: 1, 993: 1, 1020: 1, 1025: 1, 1077: 1, 1080: 11, 1101: 1, 1112: 1, 1146: 1, 1173: 1, 1185: 1, 1218: 1, 1259: 1, 1260: 2, 1261: 7, 1268: 1, 1285: 2, 1306: 1, 1379: 1, 1391: 1, 1399: 1, 1417: 1, 1429: 1, 1435: 1, 1456: 1, 1467: 1, 1470: 1, 1530: 1, 1531: 3, 1536: 3, 1539: 2, 1593: 1, 1594: 3, 1608: 3, 1629: 1, 1635: 7, 1637: 1, 1670: 9, 1676: 4, 1682: 3, 1684: 1, 1702: 4, 1723: 9, 1746: 1, 1747: 1, 1771: 1, 1774: 

In [11]:
def plot_counts(counts):
    count_values = list(counts.values())
    count_frequency = {}
    for count in count_values:
        if count in count_frequency:
            count_frequency[count] += 1
        else:
            count_frequency[count] = 1
    
    fig = go.Figure([go.Scatter(x=list(count_frequency.keys()), y=list(count_frequency.values()))])
    fig.update_layout(title='Number of Aftershocks vs Frequency', xaxis_title='Number of Aftershocks', yaxis_title='Frequency')
    fig.show()
plot_counts(num_aftershocks)


In [12]:
def is_mainshock(x):
    return x == 'b'

#creating mainshock column
etas['is_mainshock'] = etas['aftershock'].apply(is_mainshock)
etas['next_aftershock'] = etas['aftershock'].shift(-1)

In [13]:
#assign mainshock id and corresponding aftershock
def assign_mainshock_id(row):
    if row['is_mainshock']:
        #mainshock - take the integer part from the next row's 'aftershock' value
        if '.' in str(row['next_aftershock']):
            return int(str(row['next_aftershock']).split('.')[0])
        else:
            return -1  #invalid aftershock
    else:
        #aftershock - take the integer part from the current row's 'aftershock' value
        if '.' in str(row['aftershock']):
            return int(str(row['aftershock']).split('.')[0])
        else:
            return -1  #invalid aftershock


etas['mainshock_id'] = etas.apply(assign_mainshock_id, axis=1)
etas.drop('next_aftershock', axis=1, inplace=True)

In [14]:
etas['aftershock_num'] = etas['aftershock'].apply(lambda x: int(x.split('.')[1]) if x != 'b' else -1)

max_aftershock_num = etas.groupby('mainshock_id')['aftershock_num'].max().reset_index()
max_aftershock_num.rename(columns={'aftershock_num': 'max_aftershock_num'}, inplace=True)

etas = pd.merge(etas, max_aftershock_num, on='mainshock_id', how='left')

# print(etas)

In [15]:
#filter out mainshocks
mainshocks = etas.loc[etas['aftershock'] == 'b']
top_50_earthquakes = mainshocks.sort_values(by='mag', ascending=False).head(50)
# print(top_50_earthquakes)

In [16]:
fig = go.Figure(data=go.Scatter(x=top_50_earthquakes['mag'], y=top_50_earthquakes['max_aftershock_num'], mode='markers', name='Data'))
fig.update_layout(title='Magnitude vs. Number of Aftershocks',
                  xaxis_title='Magnitude',
                  yaxis_title='Number of Aftershocks')

#Quadratic Curve of Best Fit
def quadratic_model(x, a, b, c):
    return a*(x-b)**2 + c

x_data = top_50_earthquakes['mag']

popt, pcov = curve_fit(quadratic_model, x_data, top_50_earthquakes['max_aftershock_num'], p0=[3,2,-16])
a_opt, b_opt, c_opt = popt
x_model = np.linspace(min(x_data), max(x_data), 100)
y_model = quadratic_model(x_model, a_opt, b_opt, c_opt)

fig.add_trace(go.Scatter(x=x_model, y=y_model, mode='lines', name='Quadratic Curve of Best Fit'))

#Logarithmic Curve of Best Fit
def logarithmic_model(x, a, b):
    return a * np.log(x) + b

log_popt, log_pcov = curve_fit(logarithmic_model, x_data, top_50_earthquakes['max_aftershock_num'])
y_model_log = logarithmic_model(x_model, *log_popt)

fig.add_trace(go.Scatter(x=x_model, y=y_model_log, mode='lines', name='Log Curve of Best Fit'))

In [17]:
#correlation between largest earthquakes and aftershock
correlation = top_50_earthquakes['mag'].corr(top_50_earthquakes['max_aftershock_num'])
print(f"The correlation between magnitude and no. of aftershocks for large earthquakes is: {correlation}")

correlation = top_50_earthquakes['mag'].corr(np.log(top_50_earthquakes['max_aftershock_num']))
print(f"The correlation between magnitude and log of no. of aftershocks for large earthquakes is: {correlation}")

#correlation between earthquakes and aftershock
correlation = mainshocks['mag'].corr(mainshocks['max_aftershock_num'])
print(f"The general correlation between magnitude and no. of aftershocks is: {correlation}")

The correlation between magnitude and no. of aftershocks for large earthquakes is: 0.6696616324946072
The correlation between magnitude and log of no. of aftershocks for large earthquakes is: 0.9014780505192739
The general correlation between magnitude and no. of aftershocks is: 0.1732998513986612


In [18]:
fig = go.Figure(data=go.Scatter(x=top_50_earthquakes['mag'], y=np.log(top_50_earthquakes['max_aftershock_num']), mode='markers', name='Data'))
fig.update_layout(title='Magnitude vs. Number of Aftershocks (Log)',
                  xaxis_title='Magnitude',
                  yaxis_title='Number of Aftershocks')

In [19]:
def distance_calculation(lat_diff, long_diff):
    return np.sqrt(np.square(lat_diff) + np.square(long_diff))

In [20]:
#distance between main and aftershocks
etas['distance_to_mainshock'] = - 1
etas['lat_distance'] = np.nan
etas['long_distance'] = np.nan

for index, mainshock in etas[etas['aftershock'] == 'b'].iterrows():
    long = mainshock['longitude']
    lat = mainshock['latitude']
    mainshock_id = mainshock['mainshock_id']
    
    # Calculate the distance for each aftershock of this mainshock
    aftershocks = etas[(etas['mainshock_id'] == mainshock_id) & (etas['mainshock_id'] != -1)]
    for aftershock_index, aftershock in aftershocks.iterrows():
        after_long = aftershock['longitude']
        after_lat = aftershock['latitude']
        
        lat_diff = after_lat - lat
        long_diff = after_long - long
        etas.at[aftershock_index, 'lat_distance'] = lat_diff
        etas.at[aftershock_index, 'long_distance'] = long_diff
        
        etas.at[aftershock_index, 'distance_to_mainshock'] = distance_calculation(lat_diff, long_diff)


In [21]:
#max distance between main and aftershocks
etas['max_distance'] = -1

for mainshock_id in etas['mainshock_id'].unique():
    if mainshock_id == -1:
        continue
    # Find the maximum distance for this mainshock's aftershocks
    max_distance = etas[etas['mainshock_id'] == mainshock_id]['distance_to_mainshock'].max()
    # Store the maximum distance in the mainshock's row
    etas.loc[etas['mainshock_id'] == mainshock_id, 'max_distance'] = max_distance

# etas.head(20)

In [22]:
etas.to_csv('new_etas.csv')

In [23]:
fig = go.Figure(data=go.Scatter(x=etas['mainshock_id'], y=etas['distance_to_mainshock'], mode='markers', name='Data'))
fig.update_layout(title='Aftershock Distances',
                  xaxis_title='Mainshock ID',
                  yaxis_title='Distance to Mainshock')

In [24]:
fig = go.Figure(data=go.Scatter(x=etas['mainshock_id'], y=etas['max_distance'], mode='markers', name='Data'))
fig.update_layout(title='Aftershock Max Distances By Mainshock No.',
                  xaxis_title='Mainshock ID',
                  yaxis_title='Max Distance to Mainshock')

In [25]:
fig = px.scatter(etas, x="lat_distance", y="long_distance", color="mainshock_id",
                title="Spatial Diagram", width=800, height=800)
fig.update_layout(xaxis_title='X', yaxis_title='Y')
fig.show()

In [26]:
#aftershock distance for earthquakes with 10+ aftershocks
over_10_aftershocks = etas[etas['max_aftershock_num'] >= 10]
fig = px.scatter(over_10_aftershocks, x="lat_distance", y="long_distance", color="mainshock_id",
                title="Spatial Diagram (10+ Aftershocks)", width=800, height=800)
fig.update_layout(xaxis_title='X', yaxis_title='Y')
fig.show()

In [27]:
mainshocks = etas.loc[etas['aftershock'] == 'b']
top_50_earthquakes = mainshocks.sort_values(by='mag', ascending=False).head(50)

In [28]:
#correlation between largest earthquakes and aftershock
correlation = etas['mag'].corr(etas['max_distance'])
print(f"The correlation between magnitude and max aftershock distance is: {correlation}")

correlation = top_50_earthquakes['mag'].corr(top_50_earthquakes['max_distance'])
print(f"The correlation between magnitude and max aftershock distance for large earthquakes is: {correlation}")

The correlation between magnitude and max aftershock distance is: 0.16636796970120593
The correlation between magnitude and max aftershock distance for large earthquakes is: 0.05071177020487542
